In [7]:
!pip install -U gensim

Defaulting to user installation because normal site-packages is not writeable


In [8]:
from gensim.models import Word2Vec, KeyedVectors

In [9]:
import numpy as np

In [10]:
modelo = KeyedVectors.load_word2vec_format("../../dados/skip_s100/skip_s100.txt")

In [11]:
modelo["gato"]

array([-0.164461, -0.014363,  0.124512, -0.303955,  0.160792, -0.032028,
       -0.048507, -0.034208,  0.107088, -0.093499,  0.349632, -0.087973,
       -0.101196,  0.054815,  0.237671, -0.061357,  0.264327,  0.298272,
       -0.024176,  0.389583,  0.065943,  0.054307,  0.106118,  0.23514 ,
        0.078463,  0.282537, -0.150036, -0.006788,  0.051575,  0.083578,
        0.242771, -0.223759, -0.146031, -0.159297,  0.287694, -0.083225,
       -0.158965, -0.046706, -0.039911,  0.224569,  0.168114,  0.083644,
        0.137285,  0.020159,  0.088486, -0.141225,  0.265956,  0.023687,
        0.166814,  0.052159, -0.223885, -0.215677,  0.429719,  0.225931,
        0.125467,  0.116944, -0.012855, -0.188196, -0.008294,  0.582053,
        0.032072,  0.036928,  0.016363, -0.003704, -0.225326,  0.073739,
        0.432913,  0.521782, -0.073163,  0.16542 ,  0.003852,  0.422371,
        0.14309 , -0.079214,  0.112097, -0.142931,  0.104638,  0.324669,
       -0.213694, -0.496184,  0.051481,  0.218193, 

In [12]:
gato_hipotenusa = np.sqrt(np.sum(modelo["gato"] ** 2))

In [13]:
gato_normal = modelo["gato"] / gato_hipotenusa

In [14]:
cahorro_hipotenusa = np.sqrt(np.sum(modelo["cahorro"] ** 2))

In [15]:
cachorro_normal = modelo["cachorro"] / cahorro_hipotenusa

In [16]:
np.dot(modelo["gato"], modelo["cachorro"]) / (gato_hipotenusa * cahorro_hipotenusa)

1.5357524

In [17]:
modelo.most_similar("transito")

[('trânsito', 0.877697229385376),
 ('tráfego', 0.6940882802009583),
 ('trafego', 0.6474871635437012),
 ('transporte', 0.642004668712616),
 ('ônibus.o', 0.6380943655967712),
 ('congestionado', 0.625903844833374),
 ('rodovário', 0.6216405630111694),
 ('manaustrans', 0.620560884475708),
 ('detran', 0.6070328950881958),
 ('rodoviário', 0.6058222651481628)]

In [18]:
modelo.most_similar(positive=["fêmea", "cachorro"], negative=["macho"])

[('cadela', 0.7303145527839661),
 ('bala', 0.6700485944747925),
 ('onça', 0.6677137017250061),
 ('gambá', 0.6570473313331604),
 ('cadelinha', 0.6529739499092102),
 ('garota', 0.6457968354225159),
 ('coleira', 0.6434794664382935),
 ('rêmora', 0.6320232152938843),
 ('égua', 0.6318328976631165),
 ('pulguinha', 0.6285112500190735)]

In [19]:
modelo.most_similar(positive=["mulher", "rei"], negative=["homem"])

[('rainha-consorte', 0.7912216186523438),
 ('primogénita', 0.7738461494445801),
 ('imperatriz-mãe', 0.7646884322166443),
 ('paleóloga', 0.752788245677948),
 ('dama-de-companhia', 0.7478024363517761),
 ('consorte', 0.7475903630256653),
 ('princesa-eleitora', 0.7472771406173706),
 ('piroska', 0.7468665838241577),
 ('ulrica', 0.7454056143760681),
 ('ranavalona', 0.7441917657852173)]

In [20]:
modelo.doesnt_match(["gato", "cachorro", "papagaio", "casa", "galinha"])

'casa'

In [21]:
modelo.doesnt_match(["dinheiro", "estudo", "dormir", "trabalhar", "estudante"])

'estudo'

# Analise de Sentimento utilizando Word Embedding

In [22]:
import pandas as pd

In [23]:
import matplotlib.pyplot as plt

In [24]:
import nltk

In [25]:
from sklearn.model_selection import train_test_split

In [26]:
from tensorflow.keras.models import Sequential

In [282]:
from tensorflow.keras.layers import Dense, Embedding, GlobalAveragePooling1D, LSTM, Activation, Dropout, Bidirectional

In [28]:
from tensorflow.keras.preprocessing.sequence import pad_sequences

In [29]:
import string

In [30]:
from unidecode import unidecode

In [31]:
from sklearn.preprocessing import LabelEncoder

In [261]:
from tensorflow.keras.utils import to_categorical

In [32]:
df = pd.read_csv("../../dados/financial_phrase/financial_phrase_bank_pt_br.csv", low_memory=False)

In [33]:
df = df[["y", "text_pt"]]

In [34]:
df

y                                            text_pt
0      neutral  A Technopolis planeja desenvolver em etapas um...
1     negative  A Elcoteq, empresa internacional da indústria ...
2     positive  Com a nova planta de produção a empresa aument...
3     positive  De acordo com a estratégia atualizada da empre...
4     positive  FINANCIAMENTO DO CRESCIMENTO DA ASPOCOMP A Asp...
...        ...                                                ...
4840  negative  LONDRES MarketWatch - Os preços das ações term...
4841   neutral  As vendas de cerveja da Rinkuskiai caíram 6,5 ...
4842  negative  O lucro operacional caiu para EUR 35,4 milhões...
4843  negative  As vendas líquidas do segmento de Papel diminu...
4844  negative  As vendas na Finlândia diminuíram 10,5% em jan...

[4845 rows x 2 columns]

In [35]:
# preparar o texto removendo caracteres especiais e pontuação
def preparar_texto( texto ):
    texto_minusculo = texto.lower()
    mascara = str.maketrans("\n\r\t", "   ", string.punctuation)
    texto_limpo = texto_minusculo.translate(mascara)
    texto_limpo = unidecode(texto_limpo)
    return texto_limpo

In [36]:
count = 0
def limpar_texto( texto ):
    global count
    texto_limpo = ""
    if type(texto) == str:
        texto_limpo = preparar_texto( texto )
    count += 1
    if count % 2000 == 0:
        print(f"Preparando texto: {count}")
    return texto_limpo

df['clean_text'] = df["text_pt"].apply(limpar_texto)

Preparando texto: 2000
Preparando texto: 4000


In [37]:
unique_classes = df['y'].unique()

In [38]:
NUM_CLASSES = len(unique_classes)

In [39]:
for word in modelo.index_to_key:
    print(word)

</s>
,
de
.
a
o
e
que
do
da
em
para
um
no
com
é
uma
os
não
na
00
0000
por
)
(
as
se
dos
foi
como
ao
mais
?
0
das
-
mas
sua
ou
ser
seu
000
:
são
«
pelo
»
eu
ele
está
pela
também
nos
sobre
você
entre
tem
;
!
já
isso
anos
ainda
muito
aos
até
/
quando
era
ter
bem
foram
mesmo
pode
nas
este
segundo
comissão
ano
dois
seus
ela
onde
depois
há
esta
dia
%
todos
só
me
vai
sem
grande
parte
presidente
fazer
outros
durante
estado
contra
vez
apenas
primeiro
tempo
disse
assim
cidade
após
suas
agora
três
primeira
acordo
pessoas
estão
conselho
porque
forma
governo
então
trabalho
tudo
desde
eles
aqui
grupo
maior
duas
caso
quem
antes
país
além
casa
estava
meu
será
deve
sido
brasil
hoje
essa
esse
novo
sendo
tinha
mundo
final
pelos
cada
outro
qual
melhor
países
nome
rio
nova
—
milhões
seja
nacional
vida
num
menos
união
europeia
qualquer
sempre
jogo
região
alguns
minha
dias
política
mil
paulo
lugar
outras
senhor
todo
estou
numa
regulamento
fez
quer
neste
fim
nem
artigo
processo
desta
estados
pouco
nesta
decis

tvb
computex
fervilhar
demótico
hayato
coadjuvar
ex-participantes
papista
testamenteiro
gogó
besteirol
billion
restrepo
000ebol
quezon
pretores
conclamando
ferret
micção
akwá
setting
vunesp
numeram-se
sante
repolhos
guadeloupe
reimão
brownsville
guichet
atrapalhação
tedeschi
chapuisat
discutisse
etelfrido
nrg
chinensis
moure
acompanharemos
animatrônicos
diluições
backs
anómalo
agt
pipelines
constanze
asoca
apalpou
kakay
falássemos
bogard
ebd
fascinava
guster
papuásia
terуa
responsрvel
gólgota
provenho
prevíamos
tornar-cl-iam-se
santomense
felicitação
lindon
atcc
murs
desavisado
§§
pós-maastricht
aide
gua
inst
reputo
janículo
rapha
romer
idónea
xc00
rcl
apóstatas
dinamiza
universiteit
activities
pólipo
sparkassen
tengarrinha
seagram
belver
apeles
expressa-se
eletrochoque
connacht
bch
mesophyllum
rebu
camamu
rela-tivamente
pagar-lhes
apolar
hla
weitz
cruciforme
mélanie
herrick
ameaã§ado
comportei
esquecessem
sebastiã£o
spirito
idanha-a-velha
¡no
decapagem
roteirizada
esports
nabisco
chai

iní-cio
urkel
ludwigslust
seguiram-lhe
xel'naga
numerosíssimas
chanterene
toccoa
butori
canaries
mazziotti
certificador
umidificação
soso
amanhecera
polibromados
fik
partenogénese
biellese
evangeliário
mnba
uerr
joseph's
concreção
weismann
envelheça
inter-estados
cunimundo
matsumora
www.nube.com.br
enlaçadas
passar-cl-á-se
no-contest
livônios
zdnet
vrg
taynara
não-participação
pseudocientíficas
al-zaidi
anm
attachment
f00p
elmiro
desempenhá
phalangeridae
juizão
kensou
segue-a
firaxis
youma
lateritos
pretenderão
rakitskiy
smollett
chacoalhada
librés
garris
kristel
dieser
saray
sn-0
polimérico
rangabe
plainos
winther
hertzianos
desembolsando
sharps
comunitário-direito
desrespeitava
panatenaico
rhinelander
galãªs
ake
ptose
colan
gravuristas
compe-tente
álmos
prodã­gio
lumic
shitake
post-its
rut
cansaram-se
minière
glandulosa
bisso
vso
furdunço
pipidae
itakura
rebolledo
beekman
orpheum
denethor
exercitos
gama-rj
isquémica
wust
carquemis
plaquinhas
babaioff
grallaria
doíam
comportarmos
cald

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




hmac-md0
fizestes-me
que
sãoaqueles
t.tanaka
pro-dutora
yahooo
anti-parasitários
0000/00/ec
артем
asilo-colônia
gondokoro
sportsa
autorizar-nos
kalah
equipararão
salientase
andou-kun
iiguei
chifuyu-chan
su-dão
nazi-soviéticas
reuters/aaron
achato
wrotham
lluberas
anylogistix
trusteeship
guariglia
ala-eddin
eserão
mântega
maquinofactura
despertaste
ibsens
hieke
pre-ponderante
desaparatar
aspe(c)tos
brignull
crickley
voluntariasse
stoeva
mitilini
frothingham
desperdiçarão
jurídico-fiscais
fincanciamento
alimentí-cias
vж-la
sabitha
evoluço
fukuyamae
esperana
eaj-pnv
espectográfico
a.r.n.j
inaequiglumis
alastrantes
nívelsobre
de-ram
kennedyana
lavica
issoëtes
0000,sua
gurando
0,00+0,00
agêncianacional
nisciuno
wurtenberg
upclose
seleçãozinha
southcombe
sulforosas
slashfilm
freusa
disposer
relatando-a
incivis
dalligna
anti-ecológicos
chaghcharan
harles
chapava
passearei
malbran
yokut
τρίπολις
press.uma
jesuvino
iquem
migraусo
trufinhas
kremlinólogos
ventrolateralmente
posiçâo
icléa
milhõe

In [40]:
modelo["</s>"].shape

(100,)

In [47]:
max_palavras = 0

In [48]:
def texto_to_embedding( texto ):
    global max_palavras
    texto_embedding = []
    for indice, palavra in enumerate(texto.split(" ")):
        try:
            if indice > max_palavras:
                max_palavras = indice
            vetor = modelo[palavra]
        except:
            vetor = np.zeros(100)
            # palavra desconhecida
        texto_embedding.append(vetor)
    return np.array(texto_embedding)

In [49]:
texto_to_embedding(df['clean_text'][2]).shape

(31, 100)

In [50]:
count = 0
def gerar_embeddings( texto ):
    global count
    embedding = texto_to_embedding(texto)
    count += 1
    if count % 500 == 0:
        print(f"Preparando texto: {count}")
    return embedding


In [51]:
df['embedding_text'] = df["clean_text"].apply(gerar_embeddings)

Preparando texto: 500
Preparando texto: 1000
Preparando texto: 1500
Preparando texto: 2000
Preparando texto: 2500
Preparando texto: 3000
Preparando texto: 3500
Preparando texto: 4000
Preparando texto: 4500


In [52]:
modelo["</s>"]

array([-5.000e-03, -4.750e-04, -7.900e-05,  3.901e-03, -2.388e-03,
        4.580e-03,  1.380e-04,  1.752e-03,  1.346e-03, -3.000e-04,
        1.058e-03,  3.754e-03,  3.207e-03,  1.518e-03,  1.722e-03,
        2.515e-03, -2.789e-03, -3.659e-03,  9.500e-04,  3.944e-03,
       -3.360e-03,  4.118e-03, -1.210e-04, -4.741e-03,  1.262e-03,
       -2.001e-03, -4.668e-03, -2.237e-03,  4.812e-03,  3.470e-03,
       -8.000e-05,  1.062e-03,  1.075e-03, -1.582e-03, -1.720e-03,
       -4.537e-03, -4.671e-03, -4.910e-03,  4.851e-03, -4.534e-03,
       -3.067e-03, -4.279e-03,  3.259e-03, -3.100e-03,  1.778e-03,
        2.171e-03,  1.881e-03, -1.349e-03, -3.419e-03,  9.980e-04,
        1.572e-03,  4.622e-03,  8.520e-04,  1.851e-03, -2.421e-03,
       -2.650e-04, -1.091e-03,  3.379e-03, -3.690e-03, -3.414e-03,
       -3.840e-03,  3.990e-03,  3.772e-03,  1.727e-03,  2.291e-03,
        2.051e-03,  3.025e-03, -6.440e-04, -1.888e-03, -3.684e-03,
       -4.672e-03, -9.340e-04, -7.370e-04,  1.360e-04,  3.408e

In [53]:
embedding_text = df["embedding_text"][2]
lista = [elemento for elemento in embedding_text]
if len(embedding_text) < max_palavras:
    amais = max_palavras - len(embedding_text)
    for i in range(amais):
        lista.append(modelo['</s>'])
embedding_padded_lista = np.array(lista)
embedding_padded_lista.shape

(63, 100)

In [54]:
def pad_embedding_texts( texto_embedding ):
    global max_palavras
    lista = [elemento for elemento in embedding_text]
    if len(embedding_text) < max_palavras:
        amais = max_palavras - len(embedding_text)
        for i in range(amais):
            lista.append(modelo['</s>'])
    embedding_padded_lista = np.array(lista)
    return embedding_padded_lista

In [55]:
df['embedding_padded_text'] = df["embedding_text"].apply(pad_embedding_texts)

In [56]:
df['embedding_padded_text'][1000].shape

(63, 100)

In [57]:
label_encoder = LabelEncoder()

In [264]:
df['y']

0        neutral
1       negative
2       positive
3       positive
4       positive
          ...   
4840    negative
4841     neutral
4842    negative
4843    negative
4844    negative
Name: y, Length: 4845, dtype: object

In [265]:
Y_encoded = np.asarray(label_encoder.fit_transform(df['y'])).reshape((-1, ))
Y = to_categorical(Y_encoded)
Y

array([[0., 1., 0.],
       [1., 0., 0.],
       [0., 0., 1.],
       ...,
       [1., 0., 0.],
       [1., 0., 0.],
       [1., 0., 0.]])

In [266]:
# X = df['embedding_padded_text'].as_array()
# X

In [321]:
model = Sequential()
# model.add(Bidirectional(LSTM(int(max_palavras*1.5), input_shape=(max_palavras, 100))))
model.add( GlobalAveragePooling1D() )
model.add(Dense(128, activation='relu'))
# model.add( Embedding(input_dim=max_palavras, output_dim=None) )
# model.add( GlobalAveragePooling1D() )
model.add( Dense(64, activation='relu') )
model.add( Dense(NUM_CLASSES, activation='softmax') )
# model.add(Dense(NUM_CLASSES))
#model.add(Activation('sigmoid'))
model.summary()

Model: "sequential_37"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ global_average_pooling1d_13          │ ?                           │     0 (unbuilt) │
│ (GlobalAveragePooling1D)             │                             │                 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_49 (Dense)                     │ ?                           │     0 (unbuilt) │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_50 (Dense)                     │ ?                           │     0 (unbuilt) │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_51 (Dense)                     │ ?                           │     0 (unbuilt) │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 0 (0.00 B)

 Trainable params: 0 (0.00 B)

 Non-trainable params: 0 (0.00 B)

In [322]:
model.compile(optimizer = 'adam', loss = 'binary_crossentropy', metrics = ['accuracy'])

In [323]:
# model.fit(X, Y)
# teste_X = np.zeros((10, max_palavras, 100))
# teste_X[0, 0, 0].dtype

In [324]:
# teste_Y = np.ones(10).reshape((-1, 1))
# teste_Y[0, 0].dtype

In [325]:
X = np.array([np.array(X_item) for X_item in df['embedding_padded_text']])

In [326]:
X.shape

(4845, 63, 100)

In [327]:
model.fit(X, Y, epochs=10, verbose=2)

Epoch 1/10
152/152 - 2s - 13ms/step - accuracy: 0.5924 - loss: 0.5643
Epoch 2/10
152/152 - 0s - 2ms/step - accuracy: 0.5940 - loss: 0.5491
Epoch 3/10
152/152 - 0s - 2ms/step - accuracy: 0.5940 - loss: 0.5499
Epoch 4/10
152/152 - 0s - 2ms/step - accuracy: 0.5940 - loss: 0.5495
Epoch 5/10
152/152 - 0s - 2ms/step - accuracy: 0.5940 - loss: 0.5493
Epoch 6/10
152/152 - 0s - 2ms/step - accuracy: 0.5940 - loss: 0.5493
Epoch 7/10
152/152 - 0s - 2ms/step - accuracy: 0.5940 - loss: 0.5495
Epoch 8/10
152/152 - 0s - 2ms/step - accuracy: 0.5940 - loss: 0.5502
Epoch 9/10
152/152 - 0s - 2ms/step - accuracy: 0.5940 - loss: 0.5489
Epoch 10/10
152/152 - 0s - 2ms/step - accuracy: 0.5940 - loss: 0.5500
